# Hierarchical Model Tutorial


This tutorial illustrates how to use GluonTS' deep-learning based hierarchical model
`DeepVarHierarchical`. We first explain the data preparation for hierarchical/grouped time series,
and then show the model training, prediction and evaluation using common use-cases.


## Introduction

The important aspect in using hierarchical models is the proper preparation of hierarchical
time series data. The minimal requirements in building the hierarchical or grouped time series
are the time series at the bottom-level of the hierarchy and the hierarchical/grouped
aggregation matrix.
`GluonTS` provides a simple way to construct hierarchical time series by reading the bottom-level
time series and the aggregation matrix from csv files.
Here we first describe the preparation of hierarchical time series before discussing the
training of the hierarchical model.


## Preparation of Hierarchical Time Series

The bottom level time series are assumed to be available in a csv file as columns.
The csv file should also contain the index column listing the time stamps for each row.
Note that the aggregated time series are automatically constructed and should not be provided.
Here is an [example csv](https://gist.githubusercontent.com/rshyamsundar/39e57075743537c4100a716a7b7ec047/raw/f02f5aeadad73e3f3e9cf54478606d3507826492/example_bottom_ts.csv) of bottom level time series.
Similarly, the aggregation matrix can also be read from a csv file;
here is an [example](https://gist.githubusercontent.com/rshyamsundar/17084fd1f28021867bcf6f2d69d9b73a/raw/32780ca43f57a78f2d521a75e73b136b17f34a02/example_agg_mat.csv).
We use the standard format for the summation matrix;
e.g., see Eq. 10.3 of the textbook [Forecasting: Principles and Practice](https://otexts.com/fpp2/hts.html).
Note that grouped time series can also be represented by an aggregation matrix in the same
way as the hierarchical time series and hence the material presented here is also applicable to
grouped time series.

In [33]:
import numpy as np
import pandas as pd

from dataclasses import dataclass

import src.forecast.utils as utils

import plotly.express as px

In [60]:
wind_known_dyn_features = [
    "WindSpeed:100",
    "WindDirection:100",
    "WindHumidity",
    "WindTemperature",
    "WindDirection",
    "WindSpeed",
]
solar_known_dyn_features = [
    "SolarDownwardRadiation",
    "CloudCover",
    "SolarTemperature",
    # "Solar_capacity_mwp",
    # "Solar_installedcapacity_mwp",
    # "Solar_installedcapacity_mwp_pvlive",
    # "Solar_capacity_mwp_pvlive",
]
other_known_features = ["valid_data"]
wind_unknown_features = [
    "Wind_MWh_credit",
]
solar_unknown_features = [
    "Solar_MWh_credit",
]
target = "total_generation_MWh"

features = (
    wind_known_dyn_features
    + solar_known_dyn_features
    + other_known_features
    + wind_unknown_features
    + solar_unknown_features
    # + [target]
)

dataset = utils.load_dataset()
dataset = utils.filter_features(dataset, features)
input_dataset = dataset[
    [column for column in dataset.columns if column not in wind_unknown_features + solar_unknown_features]
]
input_scaler, input_dataset = utils.scale_dataset(input_dataset)
target_dataset = dataset[wind_unknown_features + solar_unknown_features] / 906
dataset = pd.concat([input_dataset, target_dataset], axis=1)
dataset = dataset[: dataset.index.max().replace(hour=22, minute=30, second=0)]
dataset.index = dataset.index.tz_localize(None)
dataset = dataset.resample("30min").mean()

In [61]:
dataset.loc[:, wind_unknown_features + solar_unknown_features].max()

Wind_MWh_credit     0.664652
Solar_MWh_credit    0.999919
dtype: float64

In [51]:
px.line(dataset.loc[:, wind_unknown_features + solar_unknown_features])

In [66]:
from gluonts.dataset.hierarchical import HierarchicalTimeSeries

S = np.array([[1, 1], [1, 0], [0, 1]])
ts_at_bottom_level = dataset[wind_unknown_features + solar_unknown_features].to_period("30min")

hts = HierarchicalTimeSeries(
    ts_at_bottom_level=ts_at_bottom_level,
    S=S,
)

One can access all the time series of the hierarchy using `ts_at_all_levels` property.

In [67]:
hts.ts_at_all_levels.head()

0         1    2
valid_datetime                           
2020-09-20 23:00  0.072300  0.072300  0.0
2020-09-20 23:30  0.062710  0.062710  0.0
2020-09-21 00:00  0.052736  0.052736  0.0
2020-09-21 00:30  0.041708  0.041708  0.0
2020-09-21 01:00  0.027493  0.027493  0.0

## Model Training and Forecasting

We now show the simplest use-case where we want to train the model on the whole dataset available
and produce predictions for the future time steps.
Note that this is how the model would be used in practice, once the best model
has already been selected based on some user-specific evaluation criteria;
see the next section for model evaluation.

We assume that the hierarchical time series `hts` of type `HierarchicalTimeSeries` has already been
constructed as described above.
The first step is to convert this hierarchical time series to a `Dataset` on which
mini-batch training can be run.
Here we convert it into `gluonts.dataset.pandas.PandasDataset`.

### Using external dynamic features

By default, the hierarchical model `DeepVarHierarchical` internally creates several time-based/dynamic
features for model training.
These are seasonal features automatically deduced from the frequency of the target time series.
One could also provide external dynamic features to the model if available.
Here we show how this is done; we restart from the point where the hierarchical time series `hts` has
already been created.

We first load the available external features from a csv file.

The dynamic features are assumed to be available both for the "training range"
(time points where the target is available) as well as for the "prediction range"
(future time points where the forecast is required).
Thus, dynamic features are longer than the target time series by `prediction_length` time steps.

For training the model, we need dynamic features only for the training range.

We create the training dataset by passing the external features `dynamic_features_df_train`
and train the model on it.

In [68]:
@dataclass
class TimeConfig:
    train_end: str = "2023-01-01 22:30:00"
    test_start: str = "2023-01-01 23:00:00"


dynamic_features_df = dataset[wind_known_dyn_features + solar_known_dyn_features + other_known_features].to_period(
    "30min"
)

dynamic_features_df_train = dynamic_features_df[: TimeConfig.train_end]
dynamic_features_df_test = dynamic_features_df[TimeConfig.test_start :]

hts_dataset_train = hts.to_dataset(feat_dynamic_real=dynamic_features_df_train)

Once the dataset is created, it is straightforward to use the hierarchical model.
Here, for a quick illustration, we fix the prediction length and choose a smaller number of epochs.
We train on the whole dataset and give the same as the input to the trained model (called predictor) to
generate predictions (or forecasts) for future/unseen time steps.
The final output `forecasts` is an instance of `gluonts.model.forecast.SampleForecast`
containing sample-based forecasts for all the time series in the hierarchy.

In [82]:
px.line(forecasts.quantile(0.5) * 906)  # .quantile_ts(0.1)

## Model Evaluation via Backtesting

We now explain how the hierarchical model can be evaluated via backtesting.
For ease of presentation, we describe the model evaluation for the case where
external dynamic features are available.
However, it is straightforward to modify the code, in case external features are not
available; simply invoke the function `to_dataset()` below without any arguments.

We assume that time series at the bottom level `ts_at_bottom_level` and the
aggregation matrix `S` have already been created as described above.
We create the train-test split along the time axis by withholding the
last `prediction_length` time points for evaluation and the remaining for training.

To generate forecasts for future/unseen time steps, we need to pass both
the past target (i.e., target in the training range) as well as
full features `dynamic_features_df` (including those in the prediction range) to the trained model.
Hence we need to create a new dataset that is separate from `dataset_train`,
unlike in the earlier case.

In [263]:
prediction_length = 48
hts_train = HierarchicalTimeSeries(
    # ts_at_bottom_level=ts_at_bottom_level[: TimeConfig.train_end],
    ts_at_bottom_level=ts_at_bottom_level.iloc[:-prediction_length, :],
    S=S,
)
hts_test_label = HierarchicalTimeSeries(
    # ts_at_bottom_level=ts_at_bottom_level[TimeConfig.test_start :],
    ts_at_bottom_level=ts_at_bottom_level.iloc[-prediction_length:, :],
    S=S,
)

We load the external features as well and slice the features corresponding to the training range.

We convert `hts_train` into `PandasDataset` by passing the external features `dynamic_features_df_train`
and train the hierarchical model on it.

In [264]:
dynamic_features_df = dataset[wind_known_dyn_features + solar_known_dyn_features + other_known_features].to_period(
    "30min"
)

# dynamic_features_df_train = dynamic_features_df[: TimeConfig.train_end]
dynamic_features_df_train = dynamic_features_df.iloc[:-prediction_length, :]
# dynamic_features_df_test = dynamic_features_df[TimeConfig.test_start :]

hts_dataset_train = hts_train.to_dataset(feat_dynamic_real=dynamic_features_df_train)
# hts_dataset_test = hts_test_label.to_dataset(feat_dynamic_real=dynamic_features_df_test)

In [ ]:
from gluonts.mx.model.deepvar_hierarchical import DeepVARHierarchicalEstimator
from gluonts.mx.trainer import Trainer

prediction_length = 48
estimator = DeepVARHierarchicalEstimator(
    freq=hts_dataset_train.freq,  # type: ignore
    prediction_length=prediction_length,
    trainer=Trainer(epochs=50, learning_rate=0.001),
    S=S,
    CRPS_weight=0.75,
    likelihood_weight=0.25,
    use_feat_dynamic_real=True,
    scaling=False,
    num_parallel_samples=100,
    batch_size=32,
    context_length=0,
)

predictor = estimator.train(hts_dataset_train)

In [262]:
from pathlib import Path
import pickle
import os

model_name = "HrDeepVar"
model_path = Path(f"./models/{model_name}")
# save the trained model in tmp/

if not os.path.isdir(model_path):
    os.mkdir(model_path)
predictor.serialize(model_path)

target_scaler = 906
with open(model_path / "target_scaler.pickle", "wb") as handle:
    pickle.dump(target_scaler, handle, protocol=pickle.HIGHEST_PROTOCOL)

with open(model_path / "input_scaler.pickle", "wb") as handle:
    pickle.dump(input_scaler, handle, protocol=pickle.HIGHEST_PROTOCOL)

To generate forecasts for time points corresponding to the
withheld observations, we need to pass full features as well as the
target in the training range to the trained model.
So we create the input dataset for the predictor accordingly
and generate forecasts.

In [274]:
predictor_input = hts_train.to_dataset(feat_dynamic_real=dynamic_features_df)
forecast_it = predictor.predict(predictor_input)

In [266]:
forecasts = []
for x in forecast_it:
    forecasts.append(x)

In [279]:
px.line(forecasts[0].quantile(0.1) * 906)  # .quantile_ts(0.1)

Once the forecasts are obtained, we can evaluate them against the withheld observations.
`GluonTS` evaluator takes as input an iterator over the true (withheld) observations and
the corresponding forecasts to do the evaluation.
Our forecasts are already in the correct format and our withheld observations are in
`hts_test_label`.

In [ ]:
from gluonts.evaluation import MultivariateEvaluator

evaluator = MultivariateEvaluator()
agg_metrics, item_metrics = evaluator(
    ts_iterator=[hts_test_label.ts_at_all_levels],
    fcst_iterator=forecast_it,
)

print(f"Mean (weighted) quantile loss over all time series: " f"{agg_metrics['mean_wQuantileLoss']}")

In [196]:
forecast = evaluator.extract_aggregate_forecast(forecast_iterator=forecast_it, agg_fun="sum")